In [2]:
library("InterSIM", quietly = TRUE)
source("runfactorization.R")

NMF - BioConductor layer [OK] | Shared memory capabilities [NO: bigmemory] | Cores 27/28

  To enable shared memory capabilities, try: install.extras('
NMF
')

Loading required package: mclust

Package 'mclust' version 5.4.6
Type 'citation("mclust")' for citing this R package in publications.

Loading required package: ade4


Attaching package: ‘ade4’


The following object is masked from ‘package:BiocGenerics’:

    score



Attaching package: ‘GPArotation’


The following object is masked from ‘package:NMF’:

    entropy



Attaching package: ‘MOFAtools’


The following objects are masked from ‘package:NMF’:

    featureNames, featureNames<-, predict, sampleNames, sampleNames<-


The following objects are masked from ‘package:Biobase’:

    featureNames, featureNames<-, sampleNames, sampleNames<-


The following object is masked from ‘package:stats’:

    predict


Loading required package: JADE

Loading required package: lattice

Loading required package: caTools

Loading required p

In [21]:
# Base folder for data
data_folder <- "../data/"
# Label to identify current run
tag <- format(Sys.time(), "%Y%m%d%H%M%S")
# Folder containing simulated data
simul_folder <- paste0(data_folder, "simulations_", tag, "/") 
# Folder for comparison results
results_folder <- paste0("../results", tag, "/")
print(data_folder)
print(tag)
print(simul_folder)
print(results_folder)
dir.create(data_folder, showWarnings = FALSE)
dir.create(simul_folder, showWarnings = FALSE)
dir.create(results_folder, showWarnings = FALSE)


[1] "../data/"
[1] "20210329212141"
[1] "../data/simulations_20210329212141/"
[1] "../results20210329212141/"


In [34]:
list_clusters <- seq(5,15,5)
list_distrib <-  c("heterogeneous","equal")

# For a given number of clusters
for(size in list_distrib) {
    thisdir1 <- paste(simul_folder,size, sep="")
    dir.create(thisdir1, showWarnings = FALSE)
    # Data distribution among clusters will either be heterogeneous or equal 
    for (num.clusters in list_clusters) {
        thisdir2 <- paste(thisdir1,"/",num.clusters, sep="")
        dir.create(thisdir2, showWarnings = FALSE)
        }
    }
        

In [35]:
## Simulate data
## INPUTS:
# folder = location  where the simulated data should be saved
# num.clusters = number of clusters to be imposed on the data
# size = heterogeneous for heterogeneous clusters, equal for equally-sized clusters
## OUPUTS: matrices of simulated data are saved to file in folder
##模拟数据
##输入：
#folder=应保存模拟数据的位置
#num.clusters =要施加在数据上的集群数
#size =对于异构集群，heterogeneous，对于相等大小的集群，equal
## OUPUTS：模拟数据矩阵保存到文件夹中的文件中
simulated_data_generation <- function(out.folder, num.clusters, size="heterogeneous", predefined=TRUE) {
    
    # Number of clusters
    num.clusters <- as.numeric(num.clusters)
    # Size of the effect
    effect <- 2.5
    # Sample proportions per clusters defined here are those used for the paper
    #此处定义的每类样本比例是本文使用的比例
    prop_predefined <- list(
        "heterogeneous" = list(
            "5" = c(0.35, 0.13, 0.19, 0.08, 0.25),
            "10" = c(0.20, 0.10, 0.07, 0.10, 0.15, 0.13, 0.10, 0.08, 0.05, 0.02),
            "15" = c(0.10,0.08,0.04,0.03,0.12,0.03,0.10,0.03,0.05,0.02,0.1,0.2,0.03,0.02,0.05)
        ),
        "equal" = list(
            "5" = c(0.25,0.2,0.2,0.2,0.15),
            "10" = c(0.15,0.1,0.1,0.1,0.1,0.1,0.05,0.1,0.1,0.1),
            "15" = c(0.07,0.07,0.07,0.06,0.07,0.07,0.07,0.06,0.07,0.06,0.07,0.06,0.07,0.06,0.07)
        )
    )

    # Check provided parameter (size) against allowed values
    if(! size %in% names(prop_predefined)) {
        print(paste0("ERROR: size can only assume value : ", 
                     paste0(names(prop_predefined), collapse=","),
                     " found : ", size))
    }

    # If article proportions are to be used
    if(predefined) {
        # Check provided parameter (number of clusters) against allowed values
        if(! as.character(num.clusters) %in% names(prop_predefined[[size]])) {
            print(paste0("ERROR: num.clusters can only assume value : ", 
                         paste0(names(prop_predefined[[size]]), collapse=","),
                         " found : ",
                         num.clusters))
        }
        prop <- prop_predefined[[size]][[as.character(num.clusters)]]
        prop[1] <- 1-sum(prop[-1])
    }
    # Otherwise
    else {
        if(size == "equal") {
            # Could be simplified! Only necessary because InterSIM is "easily offended" :
            # ensure same object type as in the heterogeneous case, and that not all 
            # values are exactly the same (should not impact the number of samples per group)
            # - same type
            equals <- rep(1, num.clusters)
            prop <- equals/sum(equals)
            # - slightly imbalanced
            delta <- 0.05*prop[1]
            prop[1] <- prop[1]+delta
            prop[num.clusters] <- prop[num.clusters]-delta
            # - sum is 1
            prop <- round(prop, digits = 10)
            prop[1] <- 1-sum(prop[-1])
        }
        else {
            random <- runif(n = num.clusters, min = 0, max = 1)
            prop <- random/sum(random)
        }
    }

    # Simulate data based on provided parameters
    print(prop)
    print(sum(prop))
    print(sum(prop)==1)
    sim.D <- InterSIM(n.sample=100, cluster.sample.prop=prop, 
                      delta.methyl=effect, delta.expr=effect, delta.protein=effect, 
                      p.DMP=0.25, p.DEG=NULL, p.DEP=NULL,
                      do.plot=FALSE, sample.cluster=TRUE, feature.cluster=TRUE)
                      
    
    thisdir <- paste(out.folder,size,"/",num.clusters, sep="")
    print(thisdir)
    #dir.create(paste(out.folder,size,num.clusters, sep="/"), showWarnings = FALSE)
    #dir.create(paste(out.folder,size,num.clusters, sep="/"), showWarnings = FALSE)
    #dir.create(paste(out.folder,size,num.clusters, sep="/"), showWarnings = FALSE)

                

    # Export simulations as tables
    write.table(sim.D$clustering.assignment, paste(thisdir, "clusters.txt", sep="/"), sep="\t")
    write_table_with_index_header(t(sim.D$dat.methyl), paste(thisdir, "omics1.txt", sep="/"))
    write_table_with_index_header(t(sim.D$dat.expr), paste(thisdir, "omics2.txt", sep="/"))
    write_table_with_index_header(t(sim.D$dat.protein), paste(thisdir, "omics3.txt", sep="/"))

    return("data saved in folder")
}

## Support function
write_table_with_index_header <- function(data, file, sep="\t") {
    write.table(cbind(probe=row.names(data),data), file, sep = sep, 
                append = FALSE, quote = FALSE, row.names = FALSE, col.names = TRUE)
}

In [36]:
## Simulate data, factorize and compare the results

list_clusters <- seq(5,15,5)
list_distrib <-  c("heterogeneous","equal")

# For a given number of clusters
for(num.clusters in list_clusters) {
    # Data distribution among clusters will either be heterogeneous or equal 
    for (size in list_distrib) {
        
        print("##########")
        print(paste0("-> Distribution: ", size, ", Nb clusters: ", num.clusters))
        
        # Make simulated data
        print("-> Simulating data...")
        simulated_data_generation(simul_folder, num.clusters, size, predefined=TRUE)
        
        print("-> Done.")
    }
}

[1] "##########"
[1] "-> Distribution: heterogeneous, Nb clusters: 5"
[1] "-> Simulating data..."
[1] 0.35 0.13 0.19 0.08 0.25
[1] 1
[1] TRUE
[1] "../data/simulations_20210329212141/heterogeneous/5"
[1] "-> Done."
[1] "##########"
[1] "-> Distribution: equal, Nb clusters: 5"
[1] "-> Simulating data..."
[1] 0.25 0.20 0.20 0.20 0.15
[1] 1
[1] TRUE
[1] "../data/simulations_20210329212141/equal/5"
[1] "-> Done."
[1] "##########"
[1] "-> Distribution: heterogeneous, Nb clusters: 10"
[1] "-> Simulating data..."
 [1] 0.20 0.10 0.07 0.10 0.15 0.13 0.10 0.08 0.05 0.02
[1] 1
[1] TRUE
[1] "../data/simulations_20210329212141/heterogeneous/10"
[1] "-> Done."
[1] "##########"
[1] "-> Distribution: equal, Nb clusters: 10"
[1] "-> Simulating data..."
 [1] 0.15 0.10 0.10 0.10 0.10 0.10 0.05 0.10 0.10 0.10
[1] 1
[1] TRUE
[1] "../data/simulations_20210329212141/equal/10"
[1] "-> Done."
[1] "##########"
[1] "-> Distribution: heterogeneous, Nb clusters: 15"
[1] "-> Simulating data..."
 [1] 0.10 0.08 0.04 0